# Hackathon #1

Topics: 
- TF Graph
- Tensors
- Sessions
- Operations
- Placeholders
- Variables
- Initialization

Some material adapted from the TensorFlow documention: https://www.tensorflow.org

This is all setup in a IPython notebook so you can run any code you want to experiment with. Feel free to edit any cell, or add some to run your own code.

In [1]:
# We'll start with our library imports...
# tensorflow to specify and run computation graphs
# numpy to run any numerical operations that need to take place outside of the TF graph
import tensorflow as tf
import numpy as np

TensorFlow programs typically consist of two sections:
1. Building the computation graph
2. Running the computation graph

A computational graph is a series of TensorFlow operations arranged into a graph of nodes. Each node takes zero or more tensors as inputs and produces a tensor as an output. This is called the tensor-in tensor-out (TITO) model, where we may think of tensors as the edges between node operations.

The basic unit of data in TensorFlow is the tensor. A tensor consists of a set of primitive values (think `float` or `int`) shaped into an array of any number of dimensions. A tensor's rank is its number of dimensions. Here are some examples of tensors:
```
3 # a rank 0 tensor; a scalar with shape []
[1., 2., 3.] # a rank 1 tensor; a vector with shape [3]
[[1., 2., 3.], [4., 5., 6.]] # a rank 2 tensor; a matrix with shape [2, 3]
[[[1., 2., 3.]], [[7., 8., 9.]]] # a rank 3 tensor with shape [2, 1, 3]
```
TF docs for `tf.Tensor`: https://www.tensorflow.org/api_docs/python/tf/Tensor

One type of graph node is a constant. TF docs for `constant`: https://www.tensorflow.org/api_docs/python/tf/constant

In [2]:
node1 = tf.constant(3.0, dtype=tf.float32)
node2 = tf.constant(4.0) # also tf.float32 implicitly
print(node1, node2)

Tensor("Const:0", shape=(), dtype=float32) Tensor("Const_1:0", shape=(), dtype=float32)


Notice that printing the nodes does not output the values `3.0` and `4.0` as you might expect.
We can see that each `Tensor` has a name, a shape, and a data type.
This is all information available statically about the `Tensor`s, before initializing the graph or running anything.

Now, we have to create a TensorFlow session in which to run our graph. TF docs for `Session`: https://www.tensorflow.org/api_docs/python/tf/Session

In [3]:
sess = tf.Session()
# This prints what we expect
print(sess.run([node1, node2]))

[3.0, 4.0]


Now we'll add an operation to the graph. TF docs for `Operation`: https://www.tensorflow.org/api_docs/python/tf/Operation

In [4]:
from __future__ import print_function
# tf.add sums the two tensors provided
node3 = tf.add(node1, node2)
print("node3:", node3)
print("sess.run(node3):", sess.run(node3))

node3: Tensor("Add:0", shape=(), dtype=float32)
sess.run(node3): 7.0


The operation is in the TF graph, so we have to run it in a sesssion to get the output. TF docs for `Session.run` https://www.tensorflow.org/versions/r0.12/api_docs/python/client/session_management#Session.run

If you visualize this subgraph in TensorBoard, it looks like this:
![img_1](https://www.tensorflow.org/images/getting_started_add.png)

Notice that when we print `node3`, it's a `Tensor`. This is following with the TITO nature of Tensorflow operations.

A graph can be parameterized to accept external inputs, known as placeholders. TF docs for `placeholder`: https://www.tensorflow.org/api_docs/python/tf/placeholder

In [5]:
a = tf.placeholder(tf.float32)
b = tf.placeholder(tf.float32)
adder_node = a + b  # + provides a shortcut for tf.add(a, b)
print("a:", a)
print("b:", b)
print("adder_node:", adder_node)

a: Tensor("Placeholder:0", dtype=float32)
b: Tensor("Placeholder_1:0", dtype=float32)
adder_node: Tensor("add:0", dtype=float32)


Many python operators are overloaded by TensorFlow to be their pointwise equivalents using numpy broadcasting. Much of the TensorFlow API closely resembles that of Numpy. Numpy docs on broadcasting: https://docs.scipy.org/doc/numpy-1.13.0/user/basics.broadcasting.html

Now, the graph looks like this:
![img_2](https://www.tensorflow.org/images/getting_started_adder.png)

In order to use operations that rely directly or indirectly on placeholders we must provide a `feed_dict` to the `Session.run` method. This is a dictionary with `placeholder` as keys and the value that they should use as the corresponding values.

In [6]:
print(sess.run(adder_node, {a: 3, b: 4.5}))
print(sess.run(adder_node, feed_dict={a: [1, 3], b: [2, 4]}))

7.5
[ 3.  7.]


Notice that, in the second `print` we feed lists for the variables. Python lists and numpy arrays can both be converted into Tensors.

We can make the computational graph more complex by adding another operation. For example:

In [7]:
add_and_triple = adder_node * 3.
print(sess.run(add_and_triple, {a: 3, b:5}))

24.0


The graph finally looks like this:
![img_3](https://www.tensorflow.org/images/getting_started_triple.png)

## Hackathon 1 Exercise 1

Write code to evaluate the function `f(x, y) = 7xy^2*cos(3x) + sqrt(5)*xy + exp(2y)` in the cell below using placeholders for `x` and `y`, and feeding values of your choice to evaluate the function in a session.

In [8]:
# Your code here

In [9]:
# Solution
x = tf.placeholder(tf.float32)
y = tf.placeholder(tf.float32)
first_term = 7. * x * tf.square(y) * tf.cos(3. * x)
second_term = tf.sqrt(5.) * x * y
third_term = tf.exp(2 * y)
fn = first_term + second_term + third_term
sess.run(fn, {x: 2., y: 3.})

537.82666

To make the model trainable, we need to be able to modify the graph to get new outputs with the same input
Variables allow us to add trainable parameters to a graph
They are constructed with a type and initial value
TF docs: https://www.tensorflow.org/api_docs/python/tf/Variable
High-level Variable How-To: https://www.tensorflow.org/programmers_guide/variables

In [10]:
W = tf.Variable([.3], dtype=tf.float32)
b = tf.Variable([-.2], dtype=tf.float32)
x = tf.placeholder(tf.float32)
linear_model = W*x + b
print("W:", W)
print("b:", b)
print("linear_model:", linear_model)

W: <tf.Variable 'Variable:0' shape=(1,) dtype=float32_ref>
b: <tf.Variable 'Variable_1:0' shape=(1,) dtype=float32_ref>
linear_model: Tensor("add_3:0", dtype=float32)


Constants are initialized when you call `tf.constant`, and their value can never change.
By contrast, variables are not initialized when you call `tf.Variable`.
To initialize all the variables in a TensorFlow program, you must explicitly call a special operation as follows.
TF docs: https://www.tensorflow.org/api_docs/python/tf/global_variables_initializer

In [11]:
init = tf.global_variables_initializer()
sess.run(init)
# Now we can do things with the values of the Variables we defined
print(sess.run([W, b]))

[array([ 0.30000001], dtype=float32), array([-0.2], dtype=float32)]


Since `x` is a placeholder, we can evaluate `linear_model` for several values of `x` simultaneously as follows.
This is also how you run more than one input at once.

In [12]:
print(sess.run(linear_model, {x: [1, 2, 3, 4]}))

[ 0.10000001  0.40000004  0.70000005  1.        ]


We've created a model, but we don't know how good it is yet.
To evaluate the model on training data, we need a `y` placeholder to provide the desired values, and we need to write a loss function.

A loss function measures how far apart the current estimated output is from the provided output.
We'll use a standard loss model for linear regression, which sums the squares of the deltas between the current model and the provided data.
`linear_model - y` creates a vector where each element is the corresponding example's error delta.
We call `tf.square` to square that error.
Then, we sum all the squared errors to create a single scalar that abstracts the error of all examples using `tf.reduce_sum`

In [13]:
y = tf.placeholder(tf.float32)
squared_deltas = tf.square(linear_model - y)
loss = tf.reduce_sum(squared_deltas)
print(sess.run(loss, {x: [1, 2, 3, 4], y: [0, -1, -2, -3]}))

25.26


We could improve this manually by reassigning the values of `W` and `b` to the perfect values of `-1` and `1`.
A variable is initialized to the value provided to `tf.Variable` but can be changed using operations like `tf.assign`.
For example, `W=-1` and `b=1` are the optimal parameters for our model. We can change `W` and `b` accordingly. TF docs for `tf.assign`: https://www.tensorflow.org/api_docs/python/tf/assign

In [14]:
fixW = tf.assign(W, [-1.])
fixb = tf.assign(b, [1.])
sess.run([fixW, fixb])
print(sess.run(loss, {x: [1, 2, 3, 4], y: [0, -1, -2, -3]}))

0.0


We guessed the "perfect" values of `W` and `b`, but the whole point of machine learning is to find the correct model parameters automatically. We will show how to accomplish this in the next Hackathon. [Click here](https://www.youtube.com/watch?v=dQw4w9WgXcQ) to see whether we're having class next Monday.